# Easy Snowflake-Python Connection using BAG data with Snowpark

## Import modules & create connection

In [1]:
### Import Snowpark for Python
from snowflake.snowpark import Session
from snowflake.snowpark.functions import col
import pandas as pd

In [2]:
### Create snowpark session to connect to saved tables (using free Personal account)
def create_session_object():
    connection_parameters = {
        "account": "YOURACCOUNTNUMBER.YOURREGION.azure",
        "user": "YOURUSERNAME",
        "password": "YOURPASSWORD",
        "role": "PUBLIC",
        "warehouse": "YOURCOMPUTEWH",
        "database": "DUTCH_ADRESSES_&_BUILDINGS_REGISTRATION_(BAG)",
        "schema": "PUBLIC"
    }
    session = Session.builder.configs(connection_parameters).create()
    print(session.sql('select current_warehouse(), current_database(), current_schema()').collect())
    return session

# Create two sessions, one for pulling the initial data, and one for pushing the udf to snowpark. Sometimes it fails just using one session
session = create_session_object()
session2 = create_session_object()

## Query the data 

In [5]:
### Example 1: Query the entire dataset
df_data = session.table('PUBLIC."Verblijfsobject_Bag"')

### Create pandas dataframe from the data
pandas_df_data = df_data.to_pandas()
pandas_df_data.head() 

In [6]:
### Example 2: Create custom query for specific number of buildings around the Tensing office in Waardenburg
df_geo = session.sql('''
    select 
        a."postcode" as "postalCode",
        a."huisnummer" as "houseNumber",
        a."huisletter" as "houseLetter",
        a."huisnummertoevoeging" as "houseNumber_add",
        b."naam" as "streetName",
        c."naam" as "townShip" ,
        d."oppervlakte" as "surfaceArea",
        d."tijdstipRegistratie" as "registrationDate",
        st_x(d."geography") as "longitude", 
        st_y(d."geography") as "latitude",
        round(st_distance(d."geography", st_makepoint(5.24822729660412, 51.83271006966607)),0) as "distanceFromOffice"
    from public."Nummeraanduiding_Bag" as a
    join public."OpenbareRuimte_Bag" as b
    on a."ligtAan" = b."identificatie"
    left join public."Woonplaats" c
    on coalesce(a."ligtIn", b."ligtIn") = c."identificatie"
    join public."Verblijfsobject_Bag" d
    on a."identificatie" = d."heeftAlsHoofdadres"
    join public."VBO_Gebruiksdoel_Bag" e
    on d."identificatie" = e."identificatie"
    and d."voorkomenidentificatie" = e."voorkomenidentificatie"
    where a."eindGeldigheid" is null
        and b."eindGeldigheid" is null
        and c."eindGeldigheid" is null
        and d."eindGeldigheid" is null
    and e."gebruiksdoel" = 'woonfunctie'
    and c."naam" = 'Waardenburg'
    order by st_distance(d."geography", st_makepoint(5.24822729660412, 51.83271006966607)),  a."postcode", a."huisnummer", a."huisletter"
    limit 5000
''')

In [7]:
### Create pandas dataframe of the queried data
pandas_df_geo = df_geo.to_pandas()
pandas_df_geo

postalCode  houseNumber houseLetter houseNumber_add     streetName  \
0       4181AH            4        None            None  Slimweistraat   
1       4181AH            5        None            None  Slimweistraat   
2       4181AH            3        None            None  Slimweistraat   
3       4181AH            6        None            None  Slimweistraat   
4       4181DA           35        None            None   Weerdenborch   
..         ...          ...         ...             ...            ...   
876     4181AL            1        None            None     Broekgraaf   
877     4181AG           18        None            None     Veerstraat   
878     4181AG           18        None            None     Veerstraat   
879     4181AG           29        None            None     Veerstraat   
880     4181AG           20        None            None     Veerstraat   

        townShip  surfaceArea registrationDate  longitude   latitude  \
0    Waardenburg          231       2022-03-02   5.246702  51.834433   
1    Waardenburg          577       2018-04-04   5.246099  51.834171   
2    Waardenburg          181       2018-01-17   5.247298  51.834708   
3    Waardenburg          125       2010-11-16   5.245314  51.833851   
4    Waardenburg          124       2010-11-16   5.251476  51.833888   
..           ...          ...              ...        ...        ...   
876  Waardenburg          159       2010-11-16   5.230243  51.850563   
877  Waardenburg          260       2022-02-23   5.221060  51.845406   
878  Waardenburg           79       2021-05-06   5.221036  51.845437   
879  Waardenburg           97       2013-03-18   5.219222  51.844011   
880  Waardenburg          180       2010-11-16   5.217035  51.843803   

     distanceFromOffice  
0                 218.0  
1                 219.0  
2                 231.0  
3                 237.0  
4                 259.0  
..                  ...  
876              2338.0  
877              2340.0  
878              2344.0  
879              2356.0  
880              2473.0  

[881 rows x 11 columns]